In [5]:
import geopandas as gpd
import folium

# Carregar o shapefile
caminho_shapefile = r"C:/Users/Marcos/Documents/Qgis - Projetos/Shapefiles/Brasil/Brasil - Uf, Me, Mi, Mu/ce1.shp"
gdf = gpd.read_file(caminho_shapefile)

# Verificar as primeiras linhas para entender como as colunas 'municipios' e 'regioes' estão
print(gdf[['municipios', 'regioes']].head())

# Criar o mapa base centrado no Ceará
latitude_ceara = -5.11
longitude_ceara = -39.17
mapa = folium.Map(location=[latitude_ceara, longitude_ceara], zoom_start=7)

# Gerar uma lista de cores para as 14 regiões
cores = ["#00FF00", "#FF5733","#E91E63", "#3F51B5", "#FF33F6", "#FFEB3B", "#009688", "#FF4081", 
"#4CAF50", "#00BCD4", "#FF9800", "#8E24AA", "#FF4081", "#33FF57"]

# Criar um dicionário que mapeia cada região para uma cor
regioes_cores = {regiao: cores[i] for i, regiao in enumerate(gdf['regioes'].unique())}

# Exibir as colunas do GeoDataFrame
print(gdf.columns)

# Adicionar o shapefile ao mapa, colorindo os municípios pela sua região
folium.GeoJson(
    gdf,
    style_function=lambda feature: {
        'fillColor': regioes_cores.get(feature['properties']['regioes'], '#FFFFFF'),  # Cor pela região
        'color': 'black',
        'weight': 0.5,
        'fillOpacity': 0.7
    },
    popup=folium.GeoJsonPopup(
        fields=['municipios', 'regioes', 'populacao', 'urbano', 'rural', 'area_km', 'modulo_fis'],
        aliases=['Município', 'Região', 'População Total', 'População Urbana (%)', 'População Rural (%)', 'Área (km²)', 'Módulo Fiscal (ha.)']
    )
).add_to(mapa)

# Adicionar o contorno dos municípios (opcional, para visualização mais clara)
folium.GeoJson(
    gdf,
    style_function=lambda x: {'fillColor': 'none', 'color': 'black', 'weight': 0.5}
).add_to(mapa)

# Adicionar a legenda personalizada, ordenando as regiões em ordem alfabética
legend_html = '''
     <div style="position: fixed; 
                 bottom: 50px; left: 50px; width: 200px; height: 375px; 
                 background-color: white; border: 2px solid grey; z-index:9999;
                 font-size: 12px; padding: 10px;">
     <b>Regiões de planejamento</b><br>
'''

# Ordenar as regiões em ordem alfabética
for regiao in sorted(regioes_cores.keys()):
    cor = regioes_cores[regiao]
    legend_html += f'<i style="background-color: {cor}; width: 18px; height: 18px; display: inline-block; margin-right: 5px;"></i> {regiao}<br>'

legend_html += '</div>'

# Adicionar a legenda ao mapa
mapa.get_root().html.add_child(folium.Element(legend_html))

# Salvar o mapa em um arquivo HTML
mapa.save("mapa1.html")
mapa

       municipios            regioes
0       Bela Cruz      Litoral Norte
1   Independência  Sertão de Crateús
2       Carnaubal  Serra da Ibiapaba
3  Senador Pompeu     Sertão Central
4           Milhã     Sertão Central
Index(['CD_GEOCMU', 'urbano', 'rural', 'municipios', 'regioes', 'populacao',
       'pop_urbana', 'pop_rural', 'area_km', 'modulo_fis', 'geometry'],
      dtype='object')
